# Tradingview to vectorbt backtest analysis

In [33]:
from numpy import sort
import vectorbt as vbt
import pandas as pd 
import datetime, pytz
from datetime import datetime, timedelta

# Read In Data

In [34]:
start_date = datetime(2018, 1, 1, tzinfo=pytz.utc)  # time period for analysis, must be timezone-aware
# end_date = datetime.now(pytz.utc)
# end_date = datetime(2020, 1, 1, tzinfo=pytz.utc)
# The following is the number of days to look back for the analysis
# time_buffer = timedelta(days=100)  # buffer before to pre-calculate SMA/EMA, best to set to max window
vbt.settings.portfolio['init_cash'] = 100_000.  # 100,000$
vbt.settings.portfolio['fees'] = 0.0025  # 0.25% # These may already be incorporated into trade file 
# vbt.settings.portfolio['commission'] = 0.0025  # 0.25% May want to use this later

# Read in the Trade File from Tradingview Strategy

In [22]:
# Download trade file from tradingview strategy as csv
trade_file_2hr = "./data/Dynamic_Wavebased_1.0_Strategy_2022-02-06 (2).csv"
trade_file_90m = "./data/Dynamic_Wavebased_1.0_Strategy_90minETHUSDT_2022-02-08.csv"
df_trades_2hr = pd.read_csv(trade_file_2hr)
df_trades_90m = pd.read_csv(trade_file_90m)

# Download Data to match the same raw price series that you were using in tradingview
The following cell we get binance data to match the tradingview data. Using the vectorbt function allows for you to update your data rather than re-downloading it. Use same frequency and ticker/exchange as what you used in your tradingview strategy for consistency

In [23]:
symbol = "ETHUSDT"
freq = '90m' 
binance_data = vbt.BinanceData.download(symbol, start=start_date, end="now UTC", interval=freq, show_progress=True) 
try: 
    binance_data.load("./data/BINANCE_ETHUSDT_2h.pickle")
    print("Loaded data from file")
except: 
    print("loading data from pickle failed")
    binance_data.get() # get data from binance first time can comment this out if you want to use the data from the csv
    binance_data.save("./data/BINANCE_ETHUSDT_2h.pickle") # save data to file this is a pickle file 
# binance_data.update() # update the data
df_data = binance_data.data["ETHUSDT"] # get the dataframe from the binance data object



2018-01-01 00:00:00+00:00 - 2022-02-08 00:00:00+00:00: : 36it [00:25,  1.40it/s]

Loaded data from file


In [24]:
# If you would like to update the data, you can do it here
binance_data.update(show_progress=True)
print("Updated data")
binance_data.save("./data/BINANCE_ETHUSDT_2h.pickle")
print("Saved data")

2022-02-08 00:00:00+00:00 - 2022-02-08 00:00:00+00:00: : 1it [00:00,  1.29it/s]

Updated data
Saved data


# Fix up the tradingview trade dataframe

In [25]:
df_data.index = df_data.index.tz_convert(None) # convert the index to tz-naive
# The following only needs to be done once after reading the trades in from tradingview
df_trades = df_trades.set_index('Date/Time')
df_trades.index = pd.to_datetime(df_trades.index)


In [26]:
# combine data and trades 

df_combined  = pd.concat([df_data, df_trades]).sort_index()

df_combined = df_combined[["Close","Price","Type","Contracts"]]
df_combined

Close  Price Type  Contracts
2018-01-01 00:00:00   717.97    NaN  NaN        NaN
2018-01-01 02:00:00   734.50    NaN  NaN        NaN
2018-01-01 04:00:00   748.99    NaN  NaN        NaN
2018-01-01 06:00:00   751.99    NaN  NaN        NaN
2018-01-01 08:00:00   753.21    NaN  NaN        NaN
...                      ...    ...  ...        ...
2022-02-07 16:00:00  3145.14    NaN  NaN        NaN
2022-02-07 18:00:00  3166.64    NaN  NaN        NaN
2022-02-07 20:00:00  3150.99    NaN  NaN        NaN
2022-02-07 22:00:00  3139.77    NaN  NaN        NaN
2022-02-08 00:00:00  3133.86    NaN  NaN        NaN

[19200 rows x 4 columns]

In [27]:
# This creates the boolean for the signals
df_combined["entries"] = df_combined["Type"] == "Entry Long"
df_combined["exits"] = df_combined["Type"] == "Exit Long"
df_combined["size"] = df_combined["Contracts"]
df_combined["short_entries"] = df_combined["Type"] == "Entry Short"
df_combined["short_exits"] = df_combined["Type"] == "Exit Short"
df_combined

Close  Price Type  Contracts  entries  exits  size  \
2018-01-01 00:00:00   717.97    NaN  NaN        NaN    False  False   NaN   
2018-01-01 02:00:00   734.50    NaN  NaN        NaN    False  False   NaN   
2018-01-01 04:00:00   748.99    NaN  NaN        NaN    False  False   NaN   
2018-01-01 06:00:00   751.99    NaN  NaN        NaN    False  False   NaN   
2018-01-01 08:00:00   753.21    NaN  NaN        NaN    False  False   NaN   
...                      ...    ...  ...        ...      ...    ...   ...   
2022-02-07 16:00:00  3145.14    NaN  NaN        NaN    False  False   NaN   
2022-02-07 18:00:00  3166.64    NaN  NaN        NaN    False  False   NaN   
2022-02-07 20:00:00  3150.99    NaN  NaN        NaN    False  False   NaN   
2022-02-07 22:00:00  3139.77    NaN  NaN        NaN    False  False   NaN   
2022-02-08 00:00:00  3133.86    NaN  NaN        NaN    False  False   NaN   

                     short_entries  short_exits  
2018-01-01 00:00:00          False        False  
2018-01-01 02:00:00          False        False  
2018-01-01 04:00:00          False        False  
2018-01-01 06:00:00          False        False  
2018-01-01 08:00:00          False        False  
...                            ...          ...  
2022-02-07 16:00:00          False        False  
2022-02-07 18:00:00          False        False  
2022-02-07 20:00:00          False        False  
2022-02-07 22:00:00          False        False  
2022-02-08 00:00:00          False        False  

[19200 rows x 9 columns]

In [28]:
df_combined["2018-01-01"]

/var/folders/xc/rshdbzdj22z7vyxh3ht1rh480000gn/T/ipykernel_40871/3206421097.py:1: FutureWarning: Indexing a DataFrame with a datetimelike index using a single string to slice the rows, like `frame[string]`, is deprecated and will be removed in a future version. Use `frame.loc[string]` instead.
  df_combined["2018-01-01"]


Close   Price         Type  Contracts  entries  exits  \
2018-01-01 00:00:00  717.97     NaN          NaN        NaN    False  False   
2018-01-01 02:00:00  734.50     NaN          NaN        NaN    False  False   
2018-01-01 04:00:00  748.99     NaN          NaN        NaN    False  False   
2018-01-01 06:00:00  751.99     NaN          NaN        NaN    False  False   
2018-01-01 08:00:00  753.21     NaN          NaN        NaN    False  False   
2018-01-01 10:00:00  741.01     NaN          NaN        NaN    False  False   
2018-01-01 12:00:00  738.93     NaN          NaN        NaN    False  False   
2018-01-01 14:00:00  748.80     NaN          NaN        NaN    False  False   
2018-01-01 16:00:00     NaN  748.27  Entry Short    80.1282    False  False   
2018-01-01 16:00:00  737.02     NaN          NaN        NaN    False  False   
2018-01-01 18:00:00  746.23     NaN          NaN        NaN    False  False   
2018-01-01 20:00:00     NaN  761.69   Entry Long    78.8924     True  False   
2018-01-01 20:00:00     NaN  761.69   Exit Short    80.1282    False  False   
2018-01-01 20:00:00  759.28     NaN          NaN        NaN    False  False   
2018-01-01 22:00:00  754.99     NaN          NaN        NaN    False  False   

                        size  short_entries  short_exits  
2018-01-01 00:00:00      NaN          False        False  
2018-01-01 02:00:00      NaN          False        False  
2018-01-01 04:00:00      NaN          False        False  
2018-01-01 06:00:00      NaN          False        False  
2018-01-01 08:00:00      NaN          False        False  
2018-01-01 10:00:00      NaN          False        False  
2018-01-01 12:00:00      NaN          False        False  
2018-01-01 14:00:00      NaN          False        False  
2018-01-01 16:00:00  80.1282           True        False  
2018-01-01 16:00:00      NaN          False        False  
2018-01-01 18:00:00      NaN          False        False  
2018-01-01 20:00:00  78.8924          False        False  
2018-01-01 20:00:00  80.1282          False         True  
2018-01-01 20:00:00      NaN          False        False  
2018-01-01 22:00:00      NaN          False        False

# @cyrus you might want to look into the "Close" column showing NaN values when there is a trade.
My hunch it has to do with the way you concatenated the two dataframes above Note there will be three of the same timestamp because there might be an entry and an exit, plus the original closing price dataframe. 

Also, it looks like we might want to pull in the "open" price or do as you did before where you shifted the close price by one. 

I see that my prices are off because the close for 14:00:00 should really be the traded price at 16:00:00 I believe. Either that or we should also pull in the `open` prices as well as the `close` so we can better portray what is really happening.

In [30]:
# Show the Long and Short signals
print(df_combined["entries"].value_counts())
print(df_combined["short_entries"].value_counts())


False    18891
True       309
Name: entries, dtype: int64
False    18879
True       321
Name: short_entries, dtype: int64


In [31]:
# Create the portfolio object

portfolio = vbt.Portfolio.from_signals(df_combined["Close"], 
                                        entries=df_combined["entries"].to_list(), 
                                        exits=df_combined["exits"].to_list(), 
                                        size=df_combined["size"].to_list(),
                                        short_entries=df_combined["short_entries"].to_list(), 
                                        short_exits=df_combined["short_exits"].to_list(), 
                                        price=df_combined['Price'].to_list(),
                                        )

In [32]:
# Show the positions and trades in a readable format
print(portfolio.positions.records_readable)

     Position Id Column        Size     Entry Timestamp  Avg Entry Price  \
0              0  Close   80.128200 2018-01-01 16:00:00           748.27   
1              1  Close   78.892400 2018-01-01 20:00:00           761.69   
2              2  Close   57.591400 2018-01-26 18:00:00          1061.31   
3              3  Close   68.427600 2018-02-16 10:00:00           919.81   
4              4  Close   66.096600 2018-02-16 22:00:00           942.09   
..           ...    ...         ...                 ...              ...   
623          623  Close  646.055900 2022-01-24 08:00:00          2386.65   
624          624  Close  322.794600 2022-01-30 20:00:00          2560.25   
625          625  Close  472.435724 2022-01-31 14:00:00          2558.41   
626          626  Close  328.753400 2022-02-02 16:00:00          2663.90   
627          627  Close  333.382800 2022-02-03 20:00:00          2665.52   

     Entry Fees      Exit Timestamp  Avg Exit Price  Exit Fees           PnL  \
0      

In [101]:
portfolio.positions.records_readable.columns

Index(['Position Id', 'Column', 'Size', 'Entry Timestamp', 'Avg Entry Price',
       'Entry Fees', 'Exit Timestamp', 'Avg Exit Price', 'Exit Fees', 'PnL',
       'Return', 'Direction', 'Status'],
      dtype='object')

In [102]:
# Show the Long and Short signals to the portfolio 
print("VectorBT thinks the portfolio has the following long and short signals: ")
print(portfolio.positions.records_readable["Direction"].value_counts()) # Check the vectorbt portfolio trades 

print("The Input Dataframe had the following information: ")
print("The Long signals are:")
print(df_combined["entries"].value_counts())

print("The Short signals are:")
print(df_combined["short_entries"].value_counts())

print("The original trades from the tradingview file are:")
print(df_trades["Type"].value_counts())

VectorBT thinks the portfolio has the following long and short signals: 
Short    319
Long     309
Name: Direction, dtype: int64
The Input Dataframe had the following information: 
The Long signals are:
False    18887
True       309
Name: entries, dtype: int64
The Short signals are:
False    18875
True       321
Name: short_entries, dtype: int64
The original trades from the tradingview file are:
Entry Short    321
Exit Short     321
Entry Long     309
Exit Long      309
Name: Type, dtype: int64


# @cyrus please look into this
It looks like we are missing 2 of our short trades. The original trade file had 321 short entries and short exits. Our VectorBT strategy thinks we only had 319 short entries. 

# Let's look at the results from VectorBT

In [18]:
# Show the portfolio statistics and compare the returns of the banchmark
bm_rets = df_combined["Close"].vbt.to_returns() # create returns dataframe for the benchmark
portfolio.stats(settings=dict(benchmark_returns=bm_rets, # Sets the benchmark returns for stats comparisons
                              frequency='2H', # Sets the frequency for stats comparisons
                              )
                )

NameError: name 'df_combined' is not defined

# @cyrus, check out the "max gross exposure" that seems like a lot of leverage
See if you can try to make sense of it all. You might need to ask for @joe's help with a spreadsheet as you try to do some forensic understanding about what is happening. 

In [106]:
print(portfolio.stats(settings=dict(benchmark_returns=bm_rets, # Sets the benchmark returns for stats comparisons
                              frequency='2H', # Sets the frequency for stats comparisons
                              )
                )
      )
portfolio.plot().show()

/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning:

Metric 'sharpe_ratio' requires frequency to be set

/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning:

Metric 'calmar_ratio' requires frequency to be set

/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning:

Metric 'omega_ratio' requires frequency to be set

/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning:

Metric 'sortino_ratio' requires frequency to be set



Start                         2018-01-01 00:00:00
End                           2022-02-07 16:00:00
Period                                      19196
Start Value                              100000.0
End Value                          1208316.644011
Total Return [%]                      1108.316644
Benchmark Return [%]                   334.867752
Max Gross Exposure [%]                 571.267454
Total Fees Paid                               0.0
Max Drawdown [%]                         18.44097
Max Drawdown Duration                      1612.0
Total Trades                                  628
Total Closed Trades                           628
Total Open Trades                               0
Open Trade PnL                                0.0
Win Rate [%]                            44.904459
Best Trade [%]                           8.826206
Worst Trade [%]                        -12.194524
Avg Winning Trade [%]                    3.749918
Avg Losing Trade [%]                    -1.978426
